In [3]:
from IPython.display import Image
from pathlib import Path
import pandas as pd
import lightgbm as lgb
from sklearn.metrics import log_loss
import math

In [4]:
train_labels = pd.read_csv("KD/train_labels_KD.csv", index_col="seq_id")
c = ['seq_id'] + ['pred_' + i for i in list(train_labels.columns)] + ['x1'] + ['pred2_' + i for i in list(train_labels.columns)] + ['x2'] +['pred3_' + i for i in list(train_labels.columns)] +['x3'] + ['insres_backgroung', 'img_count']
pred_labels = pd.read_csv("KD/insres_SER_S9.csv", index_col="seq_id", names=c)
print(len(pred_labels))
c = ['seq_id'] + ['xepred_' + i for i in list(train_labels.columns)] + ['x1'] + ['xepred2_' + i for i in list(train_labels.columns)] + ['x2'] +['xepred3_' + i for i in list(train_labels.columns)] +['x3'] + ['eff_backgroung', 'xeimg_count']
pred_labels_ce = pd.read_csv("KD/Xception_sigmoid_lr_SER_S9.csv", index_col="seq_id", names=c)
pred_labels_ce=pred_labels_ce.iloc[:len(pred_labels)]

# c = ['seq_id'] + ['effpred_' + i for i in list(train_labels.columns)] + ['x1'] + ['effpred2_' + i for i in list(train_labels.columns)] + ['x2'] +['effpred3_' + i for i in list(train_labels.columns)] +['x3'] + ['effbackgroung', 'effimg_count']
# pred_labels_eff = pd.read_csv("KD/B3_all_KD_SER_S9_.csv", index_col="seq_id", names=c).iloc[:70000]
# pred_labels_eff=pred_labels_eff.iloc[:len(pred_labels)]


del pred_labels['x1']
del pred_labels['x2']
del pred_labels['x3']

del pred_labels_ce['x1']
del pred_labels_ce['x2']
del pred_labels_ce['x3']

# del pred_labels_eff['x1']
# del pred_labels_eff['x2']
# del pred_labels_eff['x3']

367463


In [5]:
len(pred_labels), len(pred_labels_ce)

(367463, 367463)

In [6]:
join = pred_labels.join(train_labels, how='left')

In [7]:
join = join.join(pred_labels_ce, how='left')

In [8]:
# join = join.join(pred_labels_eff, how='left')

In [9]:
DATA_PATH = Path("../../datasets/wildlife") 
train_metadata = pd.read_csv(DATA_PATH / "train_metadata.csv", parse_dates= ['datetime'], index_col="seq_id")
train_metadata = train_metadata.groupby('seq_id').first()
train_metadata['month']=train_metadata.datetime.dt.month
train_metadata['hour']=train_metadata.datetime.dt.hour
join = join.join(train_metadata.hour, how='left')
join = join.join(train_metadata.month, how='left')

In [10]:
join.loc[join.img_count<3, ['pred3_' + c for c in train_labels.columns]]=-0.01
join.loc[join.img_count<2, ['pred2_' + c for c in train_labels.columns]]=-0.01
join.loc[join.img_count<3, ['xepred3_' + c for c in train_labels.columns]]=-0.01
join.loc[join.img_count<2, ['xepred2_' + c for c in train_labels.columns]]=-0.01
join.loc[join.img_count<2, ['insres_backgroung']]=-0.01
join.loc[join.img_count<2, ['eff_backgroung']]=-0.01

In [11]:
# for c in list(train_labels.columns):
#     join['median_' + c] = join[['pred_' + c, 'pred2_' + c, 'pred3_' + c, 'xepred_' + c, 'xepred2_' + c, 'xepred3_' + c]].median(axis = 1)

In [73]:
test_dataset=join.copy()

In [15]:

test_index = set(join.index[::10])
test_dataset     = join[ join.index.isin(test_index)]
trainval_dataset = join[~join.index.isin(test_index)]

val_index = set(trainval_dataset.index[::8])
val_dataset   = trainval_dataset[ trainval_dataset.index.isin(val_index)]
train_dataset = trainval_dataset[~trainval_dataset.index.isin(val_index)]
animal_columns =list(train_labels.columns)
animal_columns.remove('empty')



In [74]:
# for c in list(train_labels.columns):
#     test_dataset['pred_' + c] = (test_dataset['pred_' + c] + test_dataset['xepred_' + c]*0.1)/1.1
#     test_dataset['pred2_' + c] = (test_dataset['pred2_' + c] + test_dataset['xepred2_' + c]*0.1)/1.1
#     test_dataset['pred3_' + c] = (test_dataset['pred3_' + c] + test_dataset['xepred3_' + c]*0.1)/1.1
#     test_dataset.loc[test_dataset.img_count < 3, 'pred3_' + c]=-999
#     test_dataset.loc[test_dataset.img_count < 2, 'pred2_' + c]=-999
#     test_dataset.loc[test_dataset.img_count == 2, 'pred_' + c] = (test_dataset.loc[test_dataset.img_count == 2, 'pred_' + c] +
#                                                   test_dataset.loc[test_dataset.img_count == 2, 'pred2_' + c]*0.9) /1.9
#     test_dataset.loc[test_dataset.img_count > 2, 'pred_' + c] = (test_dataset.loc[test_dataset.img_count > 2, 'pred_' + c] +
#                                                  test_dataset.loc[test_dataset.img_count > 2, 'pred2_' +c]*0.8 +
#                                                  test_dataset.loc[test_dataset.img_count > 2, 'pred3_' + c]*0.5) / 2.3


# test_dataset['backgroung']=test_dataset['backgroung']*0.6+test_dataset['xebackgroung']*0.4
# test_dataset.loc[test_dataset.img_count==2,'pred_empty'] = (test_dataset.loc[test_dataset.img_count==2,'pred_empty']*0.6 +test_dataset.loc[test_dataset.img_count==2,'backgroung']*0.4)
# test_dataset.loc[test_dataset.img_count>2,'pred_empty'] = (test_dataset.loc[test_dataset.img_count>2,'pred_empty']*0.1 +test_dataset.loc[test_dataset.img_count>2,'backgroung']*0.9)

# backname = 'insres_backgroung' #empty 0.07279600134683438, 0.051558060196781205
# backname = 'eff_backgroung' #empty 0.07661347236099644, 0.05199410647985

# test_dataset.loc[test_dataset.img_count>1,'pred_empty'] =  (test_dataset.loc[test_dataset.img_count>1,'pred_empty'] + test_dataset.loc[test_dataset.img_count>1,'xepred_empty']*0.0)/1.0

# test_dataset.loc[test_dataset.img_count==2,'pred_empty'] = (test_dataset.loc[test_dataset.img_count==2,'pred_empty']*0.6 +test_dataset.loc[test_dataset.img_count==2,backname]*0.4)
# test_dataset.loc[test_dataset.img_count>2,'pred_empty'] = (test_dataset.loc[test_dataset.img_count>2,'pred_empty']*0.5 +test_dataset.loc[test_dataset.img_count>2,backname]*0.5)


In [71]:
len(test_dataset)

367463

In [75]:
from sklearn.metrics import log_loss
loss = 0
for c in list(train_labels.columns):
    x = test_dataset[['pred_' + c, c]].values
    if sum(x[:,1]) !=0:
        l = log_loss(x[:,1], x[:,0])
        loss+=l
        print(c, l)
print(loss/54)
# 0.00659760884180274 img1
# 0.006059572723197153 img123
# 0.0045413404802776185 img123 with bg
# 0.0045249732546423236 img123 with bg + magic

# 0.003984543177212998

aardvark 0.00019124182373379218
aardwolf 0.00032652945611576033
baboon 0.0015005172706661686
batearedfox 0.0005506364995564603
buffalo 0.004508634471176223
bushbuck 0.00017924168643919478
caracal 0.00019977975862787943
cattle 0.0006249760235581984
cheetah 0.0011983663851441778
civet 6.222032228485134e-05
dikdik 0.001049244315395914
duiker 0.0008726239623716221
eland 0.0014379133971626316
elephant 0.004861465111775876
empty 0.06787592462352943
gazellegrants 0.008288943758695697
gazellethomsons 0.020466194776325688
genet 0.00013532817925651668
giraffe 0.0037036668261533623
guineafowl 0.001784377863899967
hare 0.0005215689803173618
hartebeest 0.0035691274500877445
hippopotamus 0.0005337922148670228
honeybadger 0.00018808720052868445
hyenaspotted 0.0029230634067088663
hyenastriped 0.00029193443048684055
impala 0.004409316663291283
insectspider 0.0036500221092834045
jackal 0.001533497202911904
koribustard 0.0012731484885002541
leopard 0.00025586812822538476
lionfemale 0.0022890490829927434


In [ ]:
# zebra 0.013432987335283109 only insres zebra 0.013579589821481598
# wildebeest 0.01453010533390338 wildebeest 0.014759034644347711
# empty 0.03068587194939065  empty 0.0312
hare 0.0003635418072781709

In [56]:
classes = ['gazellethomsons', 'empty', 'zebra', 'wildebeest',  'giraffe', 'elephant', 'insectspider'] 
feature_classes=list(train_labels.columns)
# feature_classes.remove('civet')
# feature_classes.remove('bat')
# feature_classes.remove('reptiles')
# feature_classes.remove('honeybadger')

# feature_classes=[ 'monkeyvervet']


num_leaves={
    'empty': 20,
    'elephant':10,
    'gazellegrants':10,
    
}
max_depth={
    'empty': -1,
    'elephant': -1,
    'gazellegrants': -1,
}
learning_rate={
    'empty':0.01,
    'otherbird':0.001,
    'gazellegrants':0.001,
}
# columns = ['pred_' + c for c in feature_classes] +\
# ['pred2_' + c for c in feature_classes] + \
# ['pred3_' + c for c in feature_classes] + \
# ['xebackgroung', 'backgroung', 'img_count']  +\
# ['hour', 'month']

columns = ['pred_' + c for c in feature_classes] +\
['xepred_' + c for c in feature_classes] + \
['pred2_' + c for c in feature_classes] + \
['xepred2_' + c for c in feature_classes] + \
['pred3_' + c for c in feature_classes] + \
['xepred3_' + c for c in feature_classes] + \
['xebackgroung', 'backgroung', 'img_count']  +\
['hour', 'month']
# columns = ['pred_' + c for c in classes] + ['pred2_' + c for c in classes] + ['pred3_' + c for c in classes] + ['backgroung', 'img_count', 'hour', 'month']


In [51]:
clazz='hare'
X_train = train_dataset[columns]
y_train = train_dataset[clazz]
X_val = val_dataset[columns]
y_val = val_dataset[clazz]

In [52]:
# from sklearn.neighbors import KNeighborsClassifier
# from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
# from sklearn.naive_bayes import GaussianNB
# from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier
# from sklearn.gaussian_process import GaussianProcessClassifier
# from sklearn.gaussian_process.kernels import RBF
# clf = GaussianNB()
# clf.fit(X_train, y_train)
# X_test = test_dataset[columns]
# y_test = test_dataset[clazz]

# print(clazz, log_loss(y_test, clf.predict_proba(X_test.values)[:,1]))

In [53]:


lgb_train = lgb.Dataset(X_train, y_train)
lgb_val = lgb.Dataset(X_val, y_val, reference=lgb_train)

scale = y_train.mean()
if scale < 0.5:
    scale=math.log(1/scale)
else:
    scale=math.sqrt(scale)
print(scale)
params = {
        'boosting_type': 'gbdt',
        'objective': 'binary',
        'metric': {'binary_logloss'},
        'num_leaves': num_leaves.get(clazz, 5),
        'max_depth': max_depth.get(clazz, 3),
        'learning_rate': learning_rate.get(clazz, 0.01/scale),
        'feature_fraction': 0.9,
        'bagging_fraction': 0.8,
        'bagging_freq': 5,
        'verbose': 0,
#         'scale_pos_weight':scale_pos_weight.get(clazz, scale)
        'scale_pos_weight':1

}


gbm = lgb.train(params,
                    lgb_train,
                    num_boost_round=10000,
                    valid_sets=lgb_val,
                    early_stopping_rounds=50)
gbm.save_model("lgbs/" + clazz + '.txt', num_iteration=gbm.best_iteration) 

X_test = test_dataset[columns]
y_test = test_dataset[clazz]

print(clazz, log_loss(y_test, gbm.predict(X_test.values)))
# zebra 0.014600679685758957

7.190987096751118
[1]	valid_0's binary_logloss: 0.00627321
Training until validation scores don't improve for 50 rounds
[2]	valid_0's binary_logloss: 0.00539372
[3]	valid_0's binary_logloss: 0.00522213
[4]	valid_0's binary_logloss: 0.0050988
[5]	valid_0's binary_logloss: 0.00495705
[6]	valid_0's binary_logloss: 0.00483253
[7]	valid_0's binary_logloss: 0.00473147
[8]	valid_0's binary_logloss: 0.00464042
[9]	valid_0's binary_logloss: 0.00455841
[10]	valid_0's binary_logloss: 0.00449838
[11]	valid_0's binary_logloss: 0.00443074
[12]	valid_0's binary_logloss: 0.00436658
[13]	valid_0's binary_logloss: 0.00430928
[14]	valid_0's binary_logloss: 0.0042538
[15]	valid_0's binary_logloss: 0.00420228
[16]	valid_0's binary_logloss: 0.00415202
[17]	valid_0's binary_logloss: 0.00411117
[18]	valid_0's binary_logloss: 0.00406682
[19]	valid_0's binary_logloss: 0.00402425
[20]	valid_0's binary_logloss: 0.00398435
[21]	valid_0's binary_logloss: 0.00394744
[22]	valid_0's binary_logloss: 0.00391767
[23]	val

[196]	valid_0's binary_logloss: 0.00212787
[197]	valid_0's binary_logloss: 0.00212292
[198]	valid_0's binary_logloss: 0.00211801
[199]	valid_0's binary_logloss: 0.00211313
[200]	valid_0's binary_logloss: 0.00210865
[201]	valid_0's binary_logloss: 0.00210422
[202]	valid_0's binary_logloss: 0.00209982
[203]	valid_0's binary_logloss: 0.00209544
[204]	valid_0's binary_logloss: 0.00209121
[205]	valid_0's binary_logloss: 0.00208687
[206]	valid_0's binary_logloss: 0.00208269
[207]	valid_0's binary_logloss: 0.00207854
[208]	valid_0's binary_logloss: 0.00207439
[209]	valid_0's binary_logloss: 0.00207027
[210]	valid_0's binary_logloss: 0.00206617
[211]	valid_0's binary_logloss: 0.00206203
[212]	valid_0's binary_logloss: 0.00205821
[213]	valid_0's binary_logloss: 0.0020541
[214]	valid_0's binary_logloss: 0.00205002
[215]	valid_0's binary_logloss: 0.00204612
[216]	valid_0's binary_logloss: 0.00204209
[217]	valid_0's binary_logloss: 0.00203592
[218]	valid_0's binary_logloss: 0.00202994
[219]	valid_

[393]	valid_0's binary_logloss: 0.00150343
[394]	valid_0's binary_logloss: 0.00150125
[395]	valid_0's binary_logloss: 0.00149908
[396]	valid_0's binary_logloss: 0.00149699
[397]	valid_0's binary_logloss: 0.0014949
[398]	valid_0's binary_logloss: 0.00149283
[399]	valid_0's binary_logloss: 0.00149075
[400]	valid_0's binary_logloss: 0.00148857
[401]	valid_0's binary_logloss: 0.00148645
[402]	valid_0's binary_logloss: 0.00148439
[403]	valid_0's binary_logloss: 0.00148234
[404]	valid_0's binary_logloss: 0.0014803
[405]	valid_0's binary_logloss: 0.00147826
[406]	valid_0's binary_logloss: 0.00147619
[407]	valid_0's binary_logloss: 0.00147414
[408]	valid_0's binary_logloss: 0.00147209
[409]	valid_0's binary_logloss: 0.00147005
[410]	valid_0's binary_logloss: 0.00146801
[411]	valid_0's binary_logloss: 0.00146593
[412]	valid_0's binary_logloss: 0.00146386
[413]	valid_0's binary_logloss: 0.00146184
[414]	valid_0's binary_logloss: 0.00145948
[415]	valid_0's binary_logloss: 0.00145714
[416]	valid_0

[590]	valid_0's binary_logloss: 0.00116335
[591]	valid_0's binary_logloss: 0.00116172
[592]	valid_0's binary_logloss: 0.0011601
[593]	valid_0's binary_logloss: 0.00115874
[594]	valid_0's binary_logloss: 0.00115739
[595]	valid_0's binary_logloss: 0.00115578
[596]	valid_0's binary_logloss: 0.00115436
[597]	valid_0's binary_logloss: 0.00115304
[598]	valid_0's binary_logloss: 0.00115173
[599]	valid_0's binary_logloss: 0.00115042
[600]	valid_0's binary_logloss: 0.00114911
[601]	valid_0's binary_logloss: 0.00114777
[602]	valid_0's binary_logloss: 0.00114643
[603]	valid_0's binary_logloss: 0.00114509
[604]	valid_0's binary_logloss: 0.00114376
[605]	valid_0's binary_logloss: 0.00114243
[606]	valid_0's binary_logloss: 0.00114113
[607]	valid_0's binary_logloss: 0.00113984
[608]	valid_0's binary_logloss: 0.00113856
[609]	valid_0's binary_logloss: 0.00113728
[610]	valid_0's binary_logloss: 0.00113601
[611]	valid_0's binary_logloss: 0.00113465
[612]	valid_0's binary_logloss: 0.00113329
[613]	valid_

[781]	valid_0's binary_logloss: 0.000946522
[782]	valid_0's binary_logloss: 0.000945616
[783]	valid_0's binary_logloss: 0.000944711
[784]	valid_0's binary_logloss: 0.000943809
[785]	valid_0's binary_logloss: 0.000942909
[786]	valid_0's binary_logloss: 0.000941767
[787]	valid_0's binary_logloss: 0.000940843
[788]	valid_0's binary_logloss: 0.000939869
[789]	valid_0's binary_logloss: 0.000938948
[790]	valid_0's binary_logloss: 0.000938028
[791]	valid_0's binary_logloss: 0.000937133
[792]	valid_0's binary_logloss: 0.000936244
[793]	valid_0's binary_logloss: 0.000935356
[794]	valid_0's binary_logloss: 0.00093447
[795]	valid_0's binary_logloss: 0.000933581
[796]	valid_0's binary_logloss: 0.000932719
[797]	valid_0's binary_logloss: 0.00093201
[798]	valid_0's binary_logloss: 0.000931152
[799]	valid_0's binary_logloss: 0.000930295
[800]	valid_0's binary_logloss: 0.000929445
[801]	valid_0's binary_logloss: 0.000928614
[802]	valid_0's binary_logloss: 0.000927731
[803]	valid_0's binary_logloss: 0.

...

[2085]	valid_0's binary_logloss: 0.000478923
[2086]	valid_0's binary_logloss: 0.000478762
[2087]	valid_0's binary_logloss: 0.000478601
[2088]	valid_0's binary_logloss: 0.00047844
[2089]	valid_0's binary_logloss: 0.000478281
[2090]	valid_0's binary_logloss: 0.000478212
[2091]	valid_0's binary_logloss: 0.000478154
[2092]	valid_0's binary_logloss: 0.000478088
[2093]	valid_0's binary_logloss: 0.000478031
[2094]	valid_0's binary_logloss: 0.00047794
[2095]	valid_0's binary_logloss: 0.000477883
[2096]	valid_0's binary_logloss: 0.000477725
[2097]	valid_0's binary_logloss: 0.000477568
[2098]	valid_0's binary_logloss: 0.000477336
[2099]	valid_0's binary_logloss: 0.000477179
[2100]	valid_0's binary_logloss: 0.000477066
[2101]	valid_0's binary_logloss: 0.000476953
[2102]	valid_0's binary_logloss: 0.000476777
[2103]	valid_0's binary_logloss: 0.000476714
[2104]	valid_0's binary_logloss: 0.000476602
[2105]	valid_0's binary_logloss: 0.00047649
[2106]	valid_0's binary_logloss: 0.000476412
[2107]	valid_

[2269]	valid_0's binary_logloss: 0.000459733
[2270]	valid_0's binary_logloss: 0.00045968
[2271]	valid_0's binary_logloss: 0.000459585
[2272]	valid_0's binary_logloss: 0.000459493
[2273]	valid_0's binary_logloss: 0.000459398
[2274]	valid_0's binary_logloss: 0.000459303
[2275]	valid_0's binary_logloss: 0.00045921
[2276]	valid_0's binary_logloss: 0.000459086
[2277]	valid_0's binary_logloss: 0.000459069
[2278]	valid_0's binary_logloss: 0.000459052
[2279]	valid_0's binary_logloss: 0.000458929
[2280]	valid_0's binary_logloss: 0.000458806
[2281]	valid_0's binary_logloss: 0.00045875
[2282]	valid_0's binary_logloss: 0.000458694
[2283]	valid_0's binary_logloss: 0.000458638
[2284]	valid_0's binary_logloss: 0.000458583
[2285]	valid_0's binary_logloss: 0.000458493
[2286]	valid_0's binary_logloss: 0.000458494
[2287]	valid_0's binary_logloss: 0.000458496
[2288]	valid_0's binary_logloss: 0.000458498
[2289]	valid_0's binary_logloss: 0.000458501
[2290]	valid_0's binary_logloss: 0.000458503
[2291]	valid_

[2452]	valid_0's binary_logloss: 0.000443561
[2453]	valid_0's binary_logloss: 0.000443504
[2454]	valid_0's binary_logloss: 0.000443405
[2455]	valid_0's binary_logloss: 0.000443189
[2456]	valid_0's binary_logloss: 0.000443161
[2457]	valid_0's binary_logloss: 0.000443132
[2458]	valid_0's binary_logloss: 0.000443104
[2459]	valid_0's binary_logloss: 0.000443027
[2460]	valid_0's binary_logloss: 0.000442999
[2461]	valid_0's binary_logloss: 0.000442915
[2462]	valid_0's binary_logloss: 0.000442765
[2463]	valid_0's binary_logloss: 0.000442616
[2464]	valid_0's binary_logloss: 0.000442466
[2465]	valid_0's binary_logloss: 0.000442318
[2466]	valid_0's binary_logloss: 0.000442358
[2467]	valid_0's binary_logloss: 0.000442398
[2468]	valid_0's binary_logloss: 0.000442439
[2469]	valid_0's binary_logloss: 0.000442505
[2470]	valid_0's binary_logloss: 0.000442546
[2471]	valid_0's binary_logloss: 0.000442501
[2472]	valid_0's binary_logloss: 0.000442487
[2473]	valid_0's binary_logloss: 0.000442393
[2474]	val

[2641]	valid_0's binary_logloss: 0.000432134
[2642]	valid_0's binary_logloss: 0.00043208
[2643]	valid_0's binary_logloss: 0.000431966
[2644]	valid_0's binary_logloss: 0.000431897
[2645]	valid_0's binary_logloss: 0.000431843
[2646]	valid_0's binary_logloss: 0.000431797
[2647]	valid_0's binary_logloss: 0.000431784
[2648]	valid_0's binary_logloss: 0.000431738
[2649]	valid_0's binary_logloss: 0.000431693
[2650]	valid_0's binary_logloss: 0.000431647
[2651]	valid_0's binary_logloss: 0.000431515
[2652]	valid_0's binary_logloss: 0.000431383
[2653]	valid_0's binary_logloss: 0.000431351
[2654]	valid_0's binary_logloss: 0.000431205
[2655]	valid_0's binary_logloss: 0.000431073
[2656]	valid_0's binary_logloss: 0.000431111
[2657]	valid_0's binary_logloss: 0.000431086
[2658]	valid_0's binary_logloss: 0.000431126
[2659]	valid_0's binary_logloss: 0.000431163
[2660]	valid_0's binary_logloss: 0.000431201
[2661]	valid_0's binary_logloss: 0.000431159
[2662]	valid_0's binary_logloss: 0.000431118
[2663]	vali

[2828]	valid_0's binary_logloss: 0.000425981
[2829]	valid_0's binary_logloss: 0.000425938
[2830]	valid_0's binary_logloss: 0.000425924
[2831]	valid_0's binary_logloss: 0.000425874
[2832]	valid_0's binary_logloss: 0.000425823
[2833]	valid_0's binary_logloss: 0.000425747
[2834]	valid_0's binary_logloss: 0.000425697
[2835]	valid_0's binary_logloss: 0.000425665
[2836]	valid_0's binary_logloss: 0.000425652
[2837]	valid_0's binary_logloss: 0.000425667
[2838]	valid_0's binary_logloss: 0.000425675
[2839]	valid_0's binary_logloss: 0.000425684
[2840]	valid_0's binary_logloss: 0.000425693
[2841]	valid_0's binary_logloss: 0.000425735
[2842]	valid_0's binary_logloss: 0.000425778
[2843]	valid_0's binary_logloss: 0.000425831
[2844]	valid_0's binary_logloss: 0.000425874
[2845]	valid_0's binary_logloss: 0.000425872
[2846]	valid_0's binary_logloss: 0.000425911
[2847]	valid_0's binary_logloss: 0.000425874
[2848]	valid_0's binary_logloss: 0.000425834
[2849]	valid_0's binary_logloss: 0.00042579
[2850]	vali

In [38]:
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)

feature_imp = pd.DataFrame(sorted(zip(gbm.feature_importance(),X_test.columns)), columns=['Value','Feature'])
feature_imp

Value                  Feature
0        0                img_count
1        0               pred2_hare
2        0         xepred_porcupine
3        2           pred2_aardvark
4        2           pred2_mongoose
5        2            pred2_wildcat
6        2           pred_porcupine
7        2         xepred2_aardwolf
8        2     xepred2_hyenastriped
9        2          xepred2_zorilla
10       2           xepred3_duiker
11       2             xepred3_hare
12       2             xepred_genet
13       2           xepred_rodents
14       2           xepred_zorilla
15       3             pred_wildcat
16       3      xepred_hyenastriped
17       4              pred2_civet
18       4         pred3_lionfemale
19       4         pred_honeybadger
20       5             pred2_duiker
21       5           pred2_steenbok
22       5        pred3_batearedfox
23       5        pred3_honeybadger
24       5            xepred3_civet
25       5     xepred3_hyenaspotted
26       6            pred2_leopard
27       6            pred2_rodents
28       6         xepred2_aardvark
29       6      xepred2_batearedfox
30       6           xepred2_jackal
31       6         xepred3_reedbuck
32       7            xepred2_civet
33       7          xepred3_cheetah
34       7           xepred3_dikdik
35       7          xepred_aardwolf
36       7            xepred_dikdik
37       8        pred2_honeybadger
38       8               pred3_hare
39       8           xepred3_serval
40       9             pred2_dikdik
41       9           pred3_lionmale
42       9     xepred2_insectspider
43       9       xepred_honeybadger
44      10        pred_hippopotamus
45      10          xepred3_wildcat
46      11       pred3_monkeyvervet
47      11          xepred3_rodents
48      11             xepred_civet
49      11          xepred_mongoose
50      12           pred3_aardwolf
51      12              xepred2_bat
52      12          xepred2_caracal
53      12       xepred2_guineafowl
54      12         xepred3_bushbuck
55      12         xepred3_mongoose
56      13        pred2_batearedfox
57      13             pred3_serval
58      13     xepred3_hippopotamus
59      14              pred2_eland
60      14       pred2_hyenastriped
61      14             pred2_impala
62      14           pred3_steenbok
63      14             pred_rodents
64      14          xepred2_ostrich
65      14        xepred2_otherbird
66      14          xepred2_rodents
67      14             xepred2_topi
68      14          xepred3_giraffe
69      14             xepred3_topi
70      14       xepred_batearedfox
71      15             pred2_serval
72      15            pred2_vulture
73      15         pred_batearedfox
74      15              pred_dikdik
75      15                pred_hare
76      15            pred_mongoose
77      15        pred_monkeyvervet
78      15          pred_rhinoceros
79      15           xepred2_dikdik
80      15         xepred2_steenbok
81      15          xepred3_caracal
82      15       xepred3_guineafowl
83      15      xepred3_honeybadger
84      15               xepred_bat
85      16            pred2_ostrich
86      16     xepred2_hippopotamus
87      16      xepred2_honeybadger
88      16         xepred2_reptiles
89      17             pred2_jackal
90      17               pred_civet
91      17            pred_steenbok
92      17          xepred_steenbok
93      18            pred2_zorilla
94      18             pred3_dikdik
95      18       pred3_hyenastriped
96      18            pred3_zorilla
97      18             pred_zorilla
98      18        xepred3_otherbird
99      18          xepred3_vulture
100     19            pred2_caracal
101     19          xepred2_vulture
102     19            xepred_cattle
103     19           xepred_leopard
104     20      pred3_gazellegrants
105     20       pred3_hippopotamus
106     20          xepred3_buffalo
107     21                pred2_bat
108     21              pred2_genet
109     21          pred2_waterbuck
110     2

In [62]:
for clazz in list(train_labels.columns)[8:]:
    X_train = train_dataset[columns]
    y_train = train_dataset[clazz]
    if sum(y_train) < 5:
        continue
    X_val = val_dataset[columns]
    y_val = val_dataset[clazz]

    lgb_train = lgb.Dataset(X_train, y_train)
    lgb_val = lgb.Dataset(X_val, y_val, reference=lgb_train)

    scale = y_train.mean()
    if scale < 0.5:
        scale=math.log(1/scale)
    else:
        scale=math.sqrt(scale)
    print(scale)
    params = {
            'boosting_type': 'gbdt',
            'objective': 'binary',
            'metric': {'binary_logloss'},
            'num_leaves': num_leaves.get(clazz, 5),
            'max_depth': max_depth.get(clazz, 3),
            'learning_rate': learning_rate.get(clazz, 0.01/scale),
            'feature_fraction': 0.9,
            'bagging_fraction': 0.8,
            'bagging_freq': 5,
            'verbose': 0,
    #         'scale_pos_weight':scale_pos_weight.get(clazz, scale)
            'scale_pos_weight':1

    }


    gbm = lgb.train(params,
                        lgb_train,
                        num_boost_round=10000,
                        valid_sets=lgb_val,
                        early_stopping_rounds=50)
    gbm.save_model("lgbs/" + clazz + '.txt', num_iteration=gbm.best_iteration) 

    X_test = test_dataset[columns]
    y_test = test_dataset[clazz]
    if sum(y_test) ==0:
        print(clazz)
    else:
        print(clazz, log_loss(y_test, gbm.predict(X_test.values)))

10.272897066546161
[1]	valid_0's binary_logloss: 0.000780105
Training until validation scores don't improve for 50 rounds
[2]	valid_0's binary_logloss: 0.000777343
[3]	valid_0's binary_logloss: 0.000777399
[4]	valid_0's binary_logloss: 0.000774804
[5]	valid_0's binary_logloss: 0.000774833
[6]	valid_0's binary_logloss: 0.000773967
[7]	valid_0's binary_logloss: 0.000771648
[8]	valid_0's binary_logloss: 0.000769546
[9]	valid_0's binary_logloss: 0.000767629
[10]	valid_0's binary_logloss: 0.000765859
[11]	valid_0's binary_logloss: 0.0007634
[12]	valid_0's binary_logloss: 0.000763469
[13]	valid_0's binary_logloss: 0.000761276
[14]	valid_0's binary_logloss: 0.000761338
[15]	valid_0's binary_logloss: 0.000759376
[16]	valid_0's binary_logloss: 0.000755432
[17]	valid_0's binary_logloss: 0.000736313
[18]	valid_0's binary_logloss: 0.0007354
[19]	valid_0's binary_logloss: 0.00073545
[20]	valid_0's binary_logloss: 0.000731321
[21]	valid_0's binary_logloss: 0.000731365
[22]	valid_0's binary_logloss: 

[191]	valid_0's binary_logloss: 0.000694795
[192]	valid_0's binary_logloss: 0.000694837
[193]	valid_0's binary_logloss: 0.00069488
[194]	valid_0's binary_logloss: 0.000694925
[195]	valid_0's binary_logloss: 0.00069497
[196]	valid_0's binary_logloss: 0.000694555
[197]	valid_0's binary_logloss: 0.000694604
[198]	valid_0's binary_logloss: 0.000694652
[199]	valid_0's binary_logloss: 0.000694701
[200]	valid_0's binary_logloss: 0.00069475
[201]	valid_0's binary_logloss: 0.000694618
[202]	valid_0's binary_logloss: 0.000694486
[203]	valid_0's binary_logloss: 0.000694355
[204]	valid_0's binary_logloss: 0.00069411
[205]	valid_0's binary_logloss: 0.000693981
[206]	valid_0's binary_logloss: 0.000694029
[207]	valid_0's binary_logloss: 0.000694079
[208]	valid_0's binary_logloss: 0.000694128
[209]	valid_0's binary_logloss: 0.000694177
[210]	valid_0's binary_logloss: 0.000694226
[211]	valid_0's binary_logloss: 0.000694276
[212]	valid_0's binary_logloss: 0.000694326
[213]	valid_0's binary_logloss: 0.00

[381]	valid_0's binary_logloss: 0.000683313
[382]	valid_0's binary_logloss: 0.000683362
[383]	valid_0's binary_logloss: 0.000683411
[384]	valid_0's binary_logloss: 0.000683459
[385]	valid_0's binary_logloss: 0.000683508
[386]	valid_0's binary_logloss: 0.000683388
[387]	valid_0's binary_logloss: 0.000683269
[388]	valid_0's binary_logloss: 0.000683149
[389]	valid_0's binary_logloss: 0.00068303
[390]	valid_0's binary_logloss: 0.00068271
[391]	valid_0's binary_logloss: 0.000682395
[392]	valid_0's binary_logloss: 0.000682303
[393]	valid_0's binary_logloss: 0.000682187
[394]	valid_0's binary_logloss: 0.000682071
[395]	valid_0's binary_logloss: 0.000681955
[396]	valid_0's binary_logloss: 0.000682004
[397]	valid_0's binary_logloss: 0.000681923
[398]	valid_0's binary_logloss: 0.000681842
[399]	valid_0's binary_logloss: 0.000681891
[400]	valid_0's binary_logloss: 0.000681941
[401]	valid_0's binary_logloss: 0.000681993
[402]	valid_0's binary_logloss: 0.000682044
[403]	valid_0's binary_logloss: 0.

[571]	valid_0's binary_logloss: 0.000673532
[572]	valid_0's binary_logloss: 0.000673588
[573]	valid_0's binary_logloss: 0.000673643
[574]	valid_0's binary_logloss: 0.000673699
[575]	valid_0's binary_logloss: 0.000673755
Early stopping, best iteration is:
[525]	valid_0's binary_logloss: 0.000671882
cattle
7.339040196710258
[1]	valid_0's binary_logloss: 0.00520429
Training until validation scores don't improve for 50 rounds
[2]	valid_0's binary_logloss: 0.00501306
[3]	valid_0's binary_logloss: 0.00488639
[4]	valid_0's binary_logloss: 0.00478199
[5]	valid_0's binary_logloss: 0.00468908
[6]	valid_0's binary_logloss: 0.00460095
[7]	valid_0's binary_logloss: 0.00453043
[8]	valid_0's binary_logloss: 0.00446664
[9]	valid_0's binary_logloss: 0.00440635
[10]	valid_0's binary_logloss: 0.00435055
[11]	valid_0's binary_logloss: 0.00429582
[12]	valid_0's binary_logloss: 0.00424834
[13]	valid_0's binary_logloss: 0.00420036
[14]	valid_0's binary_logloss: 0.00415835
[15]	valid_0's binary_logloss: 0.004

[187]	valid_0's binary_logloss: 0.0024339
[188]	valid_0's binary_logloss: 0.00243028
[189]	valid_0's binary_logloss: 0.00242683
[190]	valid_0's binary_logloss: 0.00242293
[191]	valid_0's binary_logloss: 0.00241914
[192]	valid_0's binary_logloss: 0.0024155
[193]	valid_0's binary_logloss: 0.00241188
[194]	valid_0's binary_logloss: 0.0024083
[195]	valid_0's binary_logloss: 0.00240473
[196]	valid_0's binary_logloss: 0.00240124
[197]	valid_0's binary_logloss: 0.00239778
[198]	valid_0's binary_logloss: 0.00239438
[199]	valid_0's binary_logloss: 0.0023909
[200]	valid_0's binary_logloss: 0.00238749
[201]	valid_0's binary_logloss: 0.002384
[202]	valid_0's binary_logloss: 0.00238054
[203]	valid_0's binary_logloss: 0.00237709
[204]	valid_0's binary_logloss: 0.00237373
[205]	valid_0's binary_logloss: 0.00237032
[206]	valid_0's binary_logloss: 0.00236727
[207]	valid_0's binary_logloss: 0.00236427
[208]	valid_0's binary_logloss: 0.00236125
[209]	valid_0's binary_logloss: 0.00235831
[210]	valid_0's b

...

[2384]	valid_0's binary_logloss: 0.0141674
[2385]	valid_0's binary_logloss: 0.0141669
[2386]	valid_0's binary_logloss: 0.0141661
[2387]	valid_0's binary_logloss: 0.0141653
[2388]	valid_0's binary_logloss: 0.0141645
[2389]	valid_0's binary_logloss: 0.0141637
[2390]	valid_0's binary_logloss: 0.0141629
[2391]	valid_0's binary_logloss: 0.0141627
[2392]	valid_0's binary_logloss: 0.014162
[2393]	valid_0's binary_logloss: 0.0141614
[2394]	valid_0's binary_logloss: 0.0141612
[2395]	valid_0's binary_logloss: 0.0141605
[2396]	valid_0's binary_logloss: 0.0141599
[2397]	valid_0's binary_logloss: 0.0141591
[2398]	valid_0's binary_logloss: 0.0141584
[2399]	valid_0's binary_logloss: 0.0141576
[2400]	valid_0's binary_logloss: 0.0141568
[2401]	valid_0's binary_logloss: 0.0141561
[2402]	valid_0's binary_logloss: 0.0141556
[2403]	valid_0's binary_logloss: 0.0141554
[2404]	valid_0's binary_logloss: 0.0141549
[2405]	valid_0's binary_logloss: 0.0141544
[2406]	valid_0's binary_logloss: 0.014154
[2407]	valid_

[2575]	valid_0's binary_logloss: 0.0140887
[2576]	valid_0's binary_logloss: 0.0140876
[2577]	valid_0's binary_logloss: 0.0140874
[2578]	valid_0's binary_logloss: 0.0140868
[2579]	valid_0's binary_logloss: 0.0140861
[2580]	valid_0's binary_logloss: 0.0140859
[2581]	valid_0's binary_logloss: 0.0140856
[2582]	valid_0's binary_logloss: 0.0140854
[2583]	valid_0's binary_logloss: 0.0140852
[2584]	valid_0's binary_logloss: 0.014085
[2585]	valid_0's binary_logloss: 0.0140851
[2586]	valid_0's binary_logloss: 0.0140849
[2587]	valid_0's binary_logloss: 0.0140844
[2588]	valid_0's binary_logloss: 0.0140838
[2589]	valid_0's binary_logloss: 0.0140833
[2590]	valid_0's binary_logloss: 0.014083
[2591]	valid_0's binary_logloss: 0.0140825
[2592]	valid_0's binary_logloss: 0.0140821
[2593]	valid_0's binary_logloss: 0.0140816
[2594]	valid_0's binary_logloss: 0.0140811
[2595]	valid_0's binary_logloss: 0.0140806
[2596]	valid_0's binary_logloss: 0.0140806
[2597]	valid_0's binary_logloss: 0.0140807
[2598]	valid_

[2766]	valid_0's binary_logloss: 0.0140291
[2767]	valid_0's binary_logloss: 0.0140285
[2768]	valid_0's binary_logloss: 0.0140282
[2769]	valid_0's binary_logloss: 0.0140282
[2770]	valid_0's binary_logloss: 0.0140285
[2771]	valid_0's binary_logloss: 0.0140286
[2772]	valid_0's binary_logloss: 0.0140287
[2773]	valid_0's binary_logloss: 0.0140281
[2774]	valid_0's binary_logloss: 0.0140274
[2775]	valid_0's binary_logloss: 0.0140275
[2776]	valid_0's binary_logloss: 0.0140276
[2777]	valid_0's binary_logloss: 0.0140278
[2778]	valid_0's binary_logloss: 0.0140278
[2779]	valid_0's binary_logloss: 0.0140279
[2780]	valid_0's binary_logloss: 0.0140278
[2781]	valid_0's binary_logloss: 0.0140271
[2782]	valid_0's binary_logloss: 0.0140264
[2783]	valid_0's binary_logloss: 0.0140257
[2784]	valid_0's binary_logloss: 0.014025
[2785]	valid_0's binary_logloss: 0.0140243
[2786]	valid_0's binary_logloss: 0.0140239
[2787]	valid_0's binary_logloss: 0.0140235
[2788]	valid_0's binary_logloss: 0.0140232
[2789]	valid

[2958]	valid_0's binary_logloss: 0.0139733
[2959]	valid_0's binary_logloss: 0.0139733
[2960]	valid_0's binary_logloss: 0.0139733
[2961]	valid_0's binary_logloss: 0.0139728
[2962]	valid_0's binary_logloss: 0.0139723
[2963]	valid_0's binary_logloss: 0.0139718
[2964]	valid_0's binary_logloss: 0.0139713
[2965]	valid_0's binary_logloss: 0.0139714
[2966]	valid_0's binary_logloss: 0.0139715
[2967]	valid_0's binary_logloss: 0.0139717
[2968]	valid_0's binary_logloss: 0.0139718
[2969]	valid_0's binary_logloss: 0.0139719
[2970]	valid_0's binary_logloss: 0.013972
[2971]	valid_0's binary_logloss: 0.0139718
[2972]	valid_0's binary_logloss: 0.0139717
[2973]	valid_0's binary_logloss: 0.0139716
[2974]	valid_0's binary_logloss: 0.0139718
[2975]	valid_0's binary_logloss: 0.0139715
[2976]	valid_0's binary_logloss: 0.0139715
[2977]	valid_0's binary_logloss: 0.0139709
[2978]	valid_0's binary_logloss: 0.0139709
[2979]	valid_0's binary_logloss: 0.0139703
[2980]	valid_0's binary_logloss: 0.0139697
[2981]	valid

[3150]	valid_0's binary_logloss: 0.0139211
[3151]	valid_0's binary_logloss: 0.013921
[3152]	valid_0's binary_logloss: 0.0139206
[3153]	valid_0's binary_logloss: 0.0139206
[3154]	valid_0's binary_logloss: 0.0139205
[3155]	valid_0's binary_logloss: 0.0139204
[3156]	valid_0's binary_logloss: 0.0139205
[3157]	valid_0's binary_logloss: 0.0139206
[3158]	valid_0's binary_logloss: 0.0139206
[3159]	valid_0's binary_logloss: 0.0139209
[3160]	valid_0's binary_logloss: 0.013921
[3161]	valid_0's binary_logloss: 0.0139208
[3162]	valid_0's binary_logloss: 0.0139206
[3163]	valid_0's binary_logloss: 0.0139205
[3164]	valid_0's binary_logloss: 0.0139203
[3165]	valid_0's binary_logloss: 0.0139198
[3166]	valid_0's binary_logloss: 0.0139197
[3167]	valid_0's binary_logloss: 0.0139196
[3168]	valid_0's binary_logloss: 0.0139195
[3169]	valid_0's binary_logloss: 0.0139194
[3170]	valid_0's binary_logloss: 0.0139194
[3171]	valid_0's binary_logloss: 0.013919
[3172]	valid_0's binary_logloss: 0.013919
[3173]	valid_0'

In [65]:
X_test = test_dataset[columns]
ls = 0
c = list(train_labels.columns)
c.remove('reptiles')
for clazz in c:
    y_test = test_dataset[clazz]
    if sum(y_test) ==0 :
        print(clazz, 'bad')
        continue
    model = lgb.Booster(model_file="lgbs/" + clazz + '.txt')
    l =log_loss(y_test, model.predict(X_test))
    ls+=l
    print(clazz, l)
print(ls/54)

aardvark 9.042212816996449e-05
aardwolf 0.0005593952762478549
baboon 0.0014955021202615586
bat bad
batearedfox 0.00042493450187879777
buffalo 0.0036797415146882523
bushbuck 0.00030851912822364247
caracal 0.0002325768560325049
cattle bad
cheetah 0.0015550143257461848
civet 8.157627477884163e-05
dikdik 0.0017680783921856865
duiker 0.0006321197587348679
eland 0.0012350930878349921
elephant 0.00320123119038952
empty 0.03068587194939065
gazellegrants 0.006126928603450033
gazellethomsons 0.012815500388021745
genet 0.00032290968597748404
giraffe 0.0013331144301829741
guineafowl 0.0008990359059155418
hare 0.0003378057244948806
hartebeest 0.002035094870812233
hippopotamus 0.000880122455611693
honeybadger 4.860660621287321e-05
hyenaspotted 0.0023552066681216937
hyenastriped 0.0004927694537197797
impala 0.00415372708912369
insectspider 0.0029826606521472995
jackal 0.000967525656497379
koribustard 0.0009719732872273685
leopard 0.0005396934671154201
lionfemale 0.0024143142181912167
lionmale 0.00156

In [ ]:
aardvark 0.00014215543184568048
aardwolf 0.0004508591364472872
baboon 0.0017464964936849687
batearedfox 0.0005584773089463318
buffalo 0.004205705114248883
bushbuck 0.00013461444133176055
caracal 0.00012774976768483492
cheetah 0.0014921033821730734
civet 3.1596233544084036e-05
dikdik 0.001792085498978284
duiker 0.0008978360513132168
eland 0.001427325241307141
elephant 0.004358624955669968
empty 0.05526157837202803
gazellegrants 0.007334518590201408
gazellethomsons 0.016744181232038757
genet 0.00029686300661493925
giraffe 0.0027515076466454987
guineafowl 0.0013640892852717966
hare 0.0004629380564604658
hartebeest 0.0028042625995350116
hippopotamus 0.0006695931172353393
honeybadger 0.00010805832232163028
hyenaspotted 0.002764638317896244
hyenastriped 0.00021769289634456898
impala 0.004805353971731504
insectspider 0.003823473395375832
jackal 0.0010280228448581578
koribustard 0.0009780002268577643
leopard 0.00041891385042394153
lionfemale 0.002135840086380835
lionmale 0.0012224710031886828
mongoose 0.0003039907487659614
monkeyvervet 0.0005216045752840155
ostrich 0.0014244204261452426
otherbird 0.01330519284233979
porcupine 8.809166204356199e-05
reedbuck 0.0016403559146369786
reptiles 0.0011768364366852716
secretarybird 0.001088329233431082
serval 0.0003103944567042552
steenbok 0.00043182499834808815
topi 0.002411482378446688
vulture 0.0001957507678821575
warthog 0.004235989021126352
waterbuck 8.321889807911485e-05
wildebeest 0.01914542572062037
zebra 0.017865518797304348
0.0034590009769709116


In [61]:
list(train_labels.columns)

['aardvark',
 'aardwolf',
 'baboon',
 'bat',
 'batearedfox',
 'buffalo',
 'bushbuck',
 'caracal',
 'cattle',
 'cheetah',
 'civet',
 'dikdik',
 'duiker',
 'eland',
 'elephant',
 'empty',
 'gazellegrants',
 'gazellethomsons',
 'genet',
 'giraffe',
 'guineafowl',
 'hare',
 'hartebeest',
 'hippopotamus',
 'honeybadger',
 'hyenaspotted',
 'hyenastriped',
 'impala',
 'insectspider',
 'jackal',
 'koribustard',
 'leopard',
 'lionfemale',
 'lionmale',
 'mongoose',
 'monkeyvervet',
 'ostrich',
 'otherbird',
 'porcupine',
 'reedbuck',
 'reptiles',
 'rhinoceros',
 'rodents',
 'secretarybird',
 'serval',
 'steenbok',
 'topi',
 'vulture',
 'warthog',
 'waterbuck',
 'wildcat',
 'wildebeest',
 'zebra',
 'zorilla']